In [ ]:
!pip install diffusers peft accelerate transformers -U -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 14.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 168.3/168.3 kB 9.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 265.7/265.7 kB 16.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.2/8.2 MB 64.0 MB/s eta 0:00:00


In [ ]:
!huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    To login, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Token: 
Add token as git credential? (Y/n) Y
Token is valid (permission: write).
Cannot authenticate through git-credential as no helper is defined on your machine.
You might have to re-authenticate when pushing to the Hugging Face Hub.
Run the following command in your terminal in case you want to set the 'store' creden

In [ ]:
from diffusers import UNet2DConditionModel, AutoencoderKL, DDIMScheduler
from transformers import CLIPTextModel, CLIPTokenizer, CLIPTextModelWithProjection
import torch
from peft import LoraConfig


def get_kwargs_for_sd():
    scheduler_kwargs = {
        "beta_start": 0.00085,
        "beta_end": 0.012,
        "beta_schedule": "scaled_linear",
        "clip_sample": False,
        "set_alpha_to_one": False,
        "steps_offset": 1,
    }
    unet_kwargs = {
        "block_out_channels": (32, 64),
        "layers_per_block": 2,
        "sample_size": 32,
        "in_channels": 4,
        "out_channels": 4,
        "down_block_types": ("DownBlock2D", "CrossAttnDownBlock2D"),
        "up_block_types": ("CrossAttnUpBlock2D", "UpBlock2D"),
        "cross_attention_dim": 32,
    }
    vae_kwargs = {
        "block_out_channels": [32, 64],
        "in_channels": 3,
        "out_channels": 3,
        "down_block_types": ["DownEncoderBlock2D", "DownEncoderBlock2D"],
        "up_block_types": ["UpDecoderBlock2D", "UpDecoderBlock2D"],
        "latent_channels": 4,
    }
    return scheduler_kwargs, unet_kwargs, vae_kwargs


def get_kwargs_for_sdxl():
    scheduler_kwargs = {
        "beta_start": 0.00085,
        "beta_end": 0.012,
        "beta_schedule": "scaled_linear",
        "timestep_spacing": "leading",
        "steps_offset": 1,
    }
    unet_kwargs = {
        "block_out_channels": (32, 64),
        "layers_per_block": 2,
        "sample_size": 32,
        "in_channels": 4,
        "out_channels": 4,
        "down_block_types": ("DownBlock2D", "CrossAttnDownBlock2D"),
        "up_block_types": ("CrossAttnUpBlock2D", "UpBlock2D"),
        "attention_head_dim": (2, 4),
        "use_linear_projection": True,
        "addition_embed_type": "text_time",
        "addition_time_embed_dim": 8,
        "transformer_layers_per_block": (1, 2),
        "projection_class_embeddings_input_dim": 80,  # 6 * 8 + 32
        "cross_attention_dim": 64,
    }
    vae_kwargs = {
        "block_out_channels": [32, 64],
        "in_channels": 3,
        "out_channels": 3,
        "down_block_types": ["DownEncoderBlock2D", "DownEncoderBlock2D"],
        "up_block_types": ["UpDecoderBlock2D", "UpDecoderBlock2D"],
        "latent_channels": 4,
        "sample_size": 128,
    }

    return scheduler_kwargs, unet_kwargs, vae_kwargs

def get_dummy_components(scheduler_kwargs, unet_kwargs, vae_kwargs, has_two_text_encoders=False):
    scheduler_cls = DDIMScheduler
    rank = 4

    torch.manual_seed(0)
    unet = UNet2DConditionModel(**unet_kwargs)

    scheduler = scheduler_cls(**scheduler_kwargs)

    torch.manual_seed(0)
    vae = AutoencoderKL(**vae_kwargs)

    text_encoder = CLIPTextModel.from_pretrained("peft-internal-testing/tiny-clip-text-2")
    tokenizer = CLIPTokenizer.from_pretrained("peft-internal-testing/tiny-clip-text-2")

    if has_two_text_encoders:
        text_encoder_2 = CLIPTextModelWithProjection.from_pretrained("peft-internal-testing/tiny-clip-text-2")
        tokenizer_2 = CLIPTokenizer.from_pretrained("peft-internal-testing/tiny-clip-text-2")

    torch.manual_seed(0)
    text_lora_config = LoraConfig(
        r=rank,
        lora_alpha=rank,
        target_modules=["q_proj", "k_proj", "v_proj", "out_proj"],
        init_lora_weights=False,
    )

    torch.manual_seed(0)
    unet_lora_config = LoraConfig(
        r=rank, lora_alpha=rank, target_modules=["to_q", "to_k", "to_v", "to_out.0"], init_lora_weights=False
    )

    if has_two_text_encoders:
        pipeline_components = {
            "unet": unet,
            "scheduler": scheduler,
            "vae": vae,
            "text_encoder": text_encoder,
            "tokenizer": tokenizer,
            "text_encoder_2": text_encoder_2,
            "tokenizer_2": tokenizer_2,
            "image_encoder": None,
            "feature_extractor": None,
        }
    else:
        pipeline_components = {
            "unet": unet,
            "scheduler": scheduler,
            "vae": vae,
            "text_encoder": text_encoder,
            "tokenizer": tokenizer,
            "safety_checker": None,
            "feature_extractor": None,
            "image_encoder": None,
        }
    return pipeline_components, text_lora_config, unet_lora_config

The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

In [ ]:
from diffusers import StableDiffusionPipeline

# Handle for SD first.
scheduler_kwargs, unet_kwargs, vae_kwargs = get_kwargs_for_sd()
pipeline_components, text_lora_config, unet_lora_config = get_dummy_components(scheduler_kwargs, unet_kwargs, vae_kwargs)

sd_pipe = StableDiffusionPipeline(**pipeline_components)

config.json:   0%|          | 0.00/548 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/305k [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/752 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/11.6k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/4.78k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/133 [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/31.9k [00:00<?, ?B/s]

You have disabled the safety checker for <class 'diffusers.pipelines.stable_diffusion.pipeline_stable_diffusion.StableDiffusionPipeline'> by passing `safety_checker=None`. Ensure that you abide to the conditions of the Stable Diffusion license and do not expose unfiltered results in services or applications open to the public. Both the diffusers team and Hugging Face strongly recommend to keep the safety filter enabled in all public facing circumstances, disabling it only for use-cases that involve analyzing network behavior or auditing its results. For more information, please have a look at https://github.com/huggingface/diffusers/pull/254 .


In [ ]:
sd_pipe.push_to_hub("hf-internal-testing/tiny-sd-pipe")

'https://huggingface.co/hf-internal-testing/tiny-sd-pipe/tree/main/'

In [ ]:
from peft.utils import get_peft_model_state_dict
from diffusers.utils import convert_state_dict_to_diffusers

sd_pipe.text_encoder.add_adapter(text_lora_config)
sd_pipe.unet.add_adapter(unet_lora_config)

text_encoder_state_dict = convert_state_dict_to_diffusers(get_peft_model_state_dict(sd_pipe.text_encoder))
unet_state_dict = convert_state_dict_to_diffusers(get_peft_model_state_dict(sd_pipe.unet))

output_dir = "tiny-sd-lora-peft"
StableDiffusionPipeline.save_lora_weights(
    save_directory=output_dir,
    unet_lora_layers=unet_state_dict,
    text_encoder_lora_layers=text_encoder_state_dict,
)

In [ ]:
from diffusers import StableDiffusionXLPipeline

scheduler_kwargs, unet_kwargs, vae_kwargs = get_kwargs_for_sdxl()
pipeline_components, text_lora_config, unet_lora_config = get_dummy_components(scheduler_kwargs, unet_kwargs, vae_kwargs, has_two_text_encoders=True)

sdxl_pipe = StableDiffusionXLPipeline(**pipeline_components)

In [ ]:
sdxl_pipe.push_to_hub("hf-internal-testing/tiny-sdxl-pipe")

'https://huggingface.co/hf-internal-testing/tiny-sdxl-pipe/tree/main/'

In [ ]:
sdxl_pipe.text_encoder.add_adapter(text_lora_config)
sdxl_pipe.text_encoder_2.add_adapter(text_lora_config)
sdxl_pipe.unet.add_adapter(unet_lora_config)

text_encoder_state_dict = convert_state_dict_to_diffusers(get_peft_model_state_dict(sdxl_pipe.text_encoder))
text_encoder_2_state_dict = convert_state_dict_to_diffusers(get_peft_model_state_dict(sdxl_pipe.text_encoder_2))
unet_state_dict = convert_state_dict_to_diffusers(get_peft_model_state_dict(sdxl_pipe.unet))

output_dir = "tiny-sdxl-lora-peft"

StableDiffusionXLPipeline.save_lora_weights(
    save_directory=output_dir,
    unet_lora_layers=unet_state_dict,
    text_encoder_lora_layers=text_encoder_state_dict,
    text_encoder_2_lora_layers=text_encoder_2_state_dict,
)

In [ ]:
!ls -lh "tiny-sd-lora-peft"

total 132K
-rw-r--r-- 1 root root 130K Dec 31 14:26 pytorch_lora_weights.safetensors


In [ ]:
!ls -lh "tiny-sdxl-lora-peft"

total 272K
-rw-r--r-- 1 root root 271K Dec 31 14:26 pytorch_lora_weights.safetensors


In [ ]:
from huggingface_hub import create_repo, upload_folder

folder_path = "tiny-sd-lora-peft"
repo_id = create_repo(repo_id=f"hf-internal-testing/{folder_path}", exist_ok=True).repo_id
upload_folder(
    repo_id=repo_id, folder_path=folder_path
)

pytorch_lora_weights.safetensors:   0%|          | 0.00/132k [00:00<?, ?B/s]

'https://huggingface.co/hf-internal-testing/tiny-sd-lora-peft/tree/main/'

In [ ]:
folder_path = "tiny-sdxl-lora-peft"
filepath = f"{folder_path}/pytorch_lora_weights.safetensors"
repo_id = create_repo(repo_id=f"hf-internal-testing/{folder_path}", exist_ok=True).repo_id
upload_folder(
    repo_id=repo_id, folder_path=folder_path,
)

pytorch_lora_weights.safetensors:   0%|          | 0.00/277k [00:00<?, ?B/s]

'https://huggingface.co/hf-internal-testing/tiny-sdxl-lora-peft/tree/main/'